# Your first scraper
In this project, we will guide you step by step through the process of:

1. creating a self-contained development environment.
1. retrieving some information from an API (a website for computers)
2. leveraging it to scrape a website that does not provide an API
3. saving the output for later processing

Here we query an API for a list of countries and their past leaders. We then extract and sanitize their short bio from Wikipedia. Finally, we save the data to disk.

This task is often the first (coding) step of a datascience project and you will often come back to it in the future.

You will study topics such as *scraping*, *data structures*, *regular expressions*, *concurrency* and *file handling*. We will point out useful resources at the appropriate time. 

Let's dive in!

## 0. Creating a clean environment

Use the [`venv`](https://docs.python.org/3/library/venv.html) command to create a new environment called `wikipedia_scraper_env`.

Activate it and add it to you `.gitignore` file. 

You will find more info about virtual environments in the course content and on the web.

## 1. API Scraping

### 1a. A simple API query
You will start with the basics: how to do a simple request to an [API endpoint](../../2.python/2.python_advanced/05.Scraping/5.apis.ipynb).

You will use the [requests](https://requests.readthedocs.io/en/latest/) external library through the `import` keyword. NOTE: external libraries need to be installed first. Check the [request Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/) section of the documentation to:

1. Use the `get()` method to connect to this endpoint: https://country-leaders.onrender.com/status
2. Check if the `status_code` is equal to 200, which means OK.
    * if OK, `print()` the `text`` of the response.
    * if not, `print()` the `status_code`. 

Here is an explanation of [HTTP status codes](https://en.wikipedia.org/wiki/List_of_HTTP_status_codes).


In [1]:
import requests

api_root_url = "https://country-leaders.onrender.com"
status_endpoint = "status"

response = requests.get(f"{api_root_url}/{status_endpoint}")

if response.status_code != 200:
    print(f"Error {response.status_code} while callling API => {api_root_url}/{status_endpoint}")
else:
    print(f"Status:{response.status_code} Content:{response.content}")

Status:200 Content:b'"Alive"'


### 1b. Dealing with JSON

[JSON](https://quickref.me/json) is the preferred format to deal with data over the web. You cannot avoid it so you would better get acquainted.

Connect to another endpoint called `/countries` but this time the API will return data in the JSON format. 


In [2]:
countries_endpoint = "countries"

response = requests.get(f"{api_root_url}/{countries_endpoint}")

if response.status_code != 200:
    print(f"Error {response.status_code} while callling API => {api_root_url}/{countries_endpoint}")
else:
    print(f"Status:{response.status_code}")
    countries = response.json()
    print(countries)


Error 403 while callling API => https://country-leaders.onrender.com/countries


### 1c. Cookies anyone?

It looks like the access to this API is restricted...
Query the `/cookie` endpoint and extract the appropriate field to access your cookie.

You will need to use this cookie in each of the following API requests.

In [3]:
cookie_endpoint = "cookie"

response = requests.get(f"{api_root_url}/{cookie_endpoint}")

if response.status_code != 200:
    print(f"Error {response.status_code} while callling API => {api_root_url}/{cookie_endpoint}")
    print(response.content)
else:
    cookies = response.cookies
    print(response.cookies)


<RequestsCookieJar[<Cookie user_cookie=c98634fb-2138-4a86-aaab-c5a13e380827 for country-leaders.onrender.com/>]>


Try to query the countries endpoint using the cookie, save the output and print it.

In [4]:
response = requests.get(
    f"{api_root_url}/{countries_endpoint}",
    cookies = cookies
)

if response.status_code != 200:
    print(f"Error {response.status_code} while callling API => {api_root_url}/{countries_endpoint}")
    print(response.content)
else:
    print(f"Status:{response.status_code}")
    countries = response.json()
    print(countries)


Status:200
['fr', 'be', 'ma', 'us', 'ru']


Chances are the cookie has expired... Thanksfully, you got a nice error message. For now, simply execute the last 2 cells quickly so you get a result.

### 1d. Getting the actual data from the API

Query the `/leaders` endpoint.

In [5]:
leaders_endpoint = "leaders"

response = requests.get(
    f"{api_root_url}/{leaders_endpoint}",
    cookies = cookies
)

if response.status_code != 200:
    print(f"Error {response.status_code} while callling API => {api_root_url}/{leaders_endpoint}")
    print(response.content)
else:
    leaders = response.json()
    print(leaders)


Error 404 while callling API => https://country-leaders.onrender.com/leaders
b'{"message":"Please specify a country"}'


It looks like this endpoint requires additional information in order to return its result. Check the API [*documentation*](https://country-leaders.onrender.com/docs) in your web browser.

Change the query to accept *parameters*. You should know where to find help by now.

In [6]:
response = requests.get(
    f"{api_root_url}/{leaders_endpoint}",
    cookies = cookies,
    params = {"country": countries[0]}
)

if response.status_code != 200:
    print(f"Error {response.status_code} while callling API => {api_root_url}/{leaders_endpoint}")
    print(response.content)
else:
    leaders = response.json()
    print(f"Leadders of {countries[0]}")
    print(leaders)

Leadders of fr
[{'id': 'Q157', 'first_name': 'François', 'last_name': 'Hollande', 'birth_date': '1954-08-12', 'death_date': None, 'place_of_birth': 'Rouen', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Hollande', 'start_mandate': '2012-05-15', 'end_mandate': '2017-05-14'}, {'id': 'Q329', 'first_name': 'Nicolas', 'last_name': 'Sarkozy', 'birth_date': '1955-01-28', 'death_date': None, 'place_of_birth': 'Paris', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Nicolas_Sarkozy', 'start_mandate': '2007-05-16', 'end_mandate': '2012-05-15'}, {'id': 'Q2038', 'first_name': 'François', 'last_name': 'Mitterrand', 'birth_date': '1916-10-26', 'death_date': '1996-01-08', 'place_of_birth': 'Jarnac', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Mitterrand', 'start_mandate': '1981-05-21', 'end_mandate': '1995-05-17'}, {'id': 'Q2042', 'first_name': 'Charles', 'last_name': 'de Gaulle', 'birth_date': '1890-11-22', 'death_date': '1970-11-09', 'place_of_birth': 'Lille', 'wik

### 1e. A sneak peak at the data (finally)

Look inside a few examples. Notice the dictionary keys available for each entry. You have your first example of *structured data*. This data was sanitized for your benefit, meaning it is readily exploitable without modification.

You will also notice there is a Wikipedia link for each entry. You will need to extract additional information there. This will be a case of *semi-structured* data.

The /countries endpoint returns a `list` of several country codes.

You need to loop through this list and query the /leaders endpoint for each one. Save each `json` result in a dictionary called `leaders_per_country`.

In [7]:
leaders_per_country = {}

for country in countries:
    response = requests.get(
        f"{api_root_url}/{leaders_endpoint}",
        cookies = cookies,
        params = {"country": country}
    )
    if response.status_code == 200:
        leaders_per_country[country] = response.json()

print(leaders_per_country)

{'fr': [{'id': 'Q157', 'first_name': 'François', 'last_name': 'Hollande', 'birth_date': '1954-08-12', 'death_date': None, 'place_of_birth': 'Rouen', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Hollande', 'start_mandate': '2012-05-15', 'end_mandate': '2017-05-14'}, {'id': 'Q329', 'first_name': 'Nicolas', 'last_name': 'Sarkozy', 'birth_date': '1955-01-28', 'death_date': None, 'place_of_birth': 'Paris', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Nicolas_Sarkozy', 'start_mandate': '2007-05-16', 'end_mandate': '2012-05-15'}, {'id': 'Q2038', 'first_name': 'François', 'last_name': 'Mitterrand', 'birth_date': '1916-10-26', 'death_date': '1996-01-08', 'place_of_birth': 'Jarnac', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Mitterrand', 'start_mandate': '1981-05-21', 'end_mandate': '1995-05-17'}, {'id': 'Q2042', 'first_name': 'Charles', 'last_name': 'de Gaulle', 'birth_date': '1890-11-22', 'death_date': '1970-11-09', 'place_of_birth': 'Lille', 'wikipedia_u

In [8]:
leaders_per_country = {
    country: resp.json()
    for country in countries
    if (resp := requests.get(
        f"{api_root_url}/{leaders_endpoint}",
        cookies = cookies,
        params = {"country": country}
    )).status_code == 200
}

print(leaders_per_country)

{'fr': [{'id': 'Q157', 'first_name': 'François', 'last_name': 'Hollande', 'birth_date': '1954-08-12', 'death_date': None, 'place_of_birth': 'Rouen', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Hollande', 'start_mandate': '2012-05-15', 'end_mandate': '2017-05-14'}, {'id': 'Q329', 'first_name': 'Nicolas', 'last_name': 'Sarkozy', 'birth_date': '1955-01-28', 'death_date': None, 'place_of_birth': 'Paris', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Nicolas_Sarkozy', 'start_mandate': '2007-05-16', 'end_mandate': '2012-05-15'}, {'id': 'Q2038', 'first_name': 'François', 'last_name': 'Mitterrand', 'birth_date': '1916-10-26', 'death_date': '1996-01-08', 'place_of_birth': 'Jarnac', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Mitterrand', 'start_mandate': '1981-05-21', 'end_mandate': '1995-05-17'}, {'id': 'Q2042', 'first_name': 'Charles', 'last_name': 'de Gaulle', 'birth_date': '1890-11-22', 'death_date': '1970-11-09', 'place_of_birth': 'Lille', 'wikipedia_u

It is finally time to create a `get_leaders()` function for the above code. You will build on it later-on. This function takes no parameter. Inside it, you will need to:
1. define the urls
2. get the cookies
2. get the countries
3. loop over them and save their leaders in a dictionary
4. return the dictionary

In [9]:
def get_leaders():
    api_root_url = "https://country-leaders.onrender.com"
    cookie_endpoint = "cookie"
    countries_endpoint = "countries"
    leaders_endpoint = "leaders"

    cookie_response = requests.get(f"{api_root_url}/{cookie_endpoint}")

    if cookie_response.status_code != 200:
        print(f"Error {cookie_response.status_code} while callling API => {api_root_url}/{cookie_endpoint}")
        return None
    
    cookies = cookie_response.cookies

    countries_response = requests.get(
        f"{api_root_url}/{countries_endpoint}",
        cookies = cookies
    )

    if countries_response.status_code != 200:
        print(f"Error {countries_response.status_code} while callling API => {api_root_url}/{countries_endpoint}")
        print(countries_response.content)
        return None

    countries = countries_response.json()
    leaders_per_country = {}

    for country in countries:
        leaders_response = requests.get(
            f"{api_root_url}/{leaders_endpoint}",
            cookies = cookies,
            params = {"country": country}
        )
        if leaders_response.status_code == 200:
            leaders_per_country[country] = leaders_response.json()
    
    return leaders_per_country


Test your function, save the result in the `leaders_per_country` dictionary and check its ouput.

In [10]:
leaders_per_country = get_leaders()

print(leaders_per_country)


{'fr': [{'id': 'Q157', 'first_name': 'François', 'last_name': 'Hollande', 'birth_date': '1954-08-12', 'death_date': None, 'place_of_birth': 'Rouen', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Hollande', 'start_mandate': '2012-05-15', 'end_mandate': '2017-05-14'}, {'id': 'Q329', 'first_name': 'Nicolas', 'last_name': 'Sarkozy', 'birth_date': '1955-01-28', 'death_date': None, 'place_of_birth': 'Paris', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Nicolas_Sarkozy', 'start_mandate': '2007-05-16', 'end_mandate': '2012-05-15'}, {'id': 'Q2038', 'first_name': 'François', 'last_name': 'Mitterrand', 'birth_date': '1916-10-26', 'death_date': '1996-01-08', 'place_of_birth': 'Jarnac', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Mitterrand', 'start_mandate': '1981-05-21', 'end_mandate': '1995-05-17'}, {'id': 'Q2042', 'first_name': 'Charles', 'last_name': 'de Gaulle', 'birth_date': '1890-11-22', 'death_date': '1970-11-09', 'place_of_birth': 'Lille', 'wikipedia_u

## 2. Extracting data from Wikipedia

Query one of the leaders' Wikipedia urls and display its `text` (not JSON).

In [11]:
first_french_leader = leaders_per_country["fr"][0]

wiki_response = requests.get(first_french_leader["wikipedia_url"])
wiki_html = wiki_response.content
print(wiki_html)


b'<!DOCTYPE html>\n<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-sticky-header-enabled vector-toc-available" lang="fr" dir="ltr">\n<head>\n<meta charset="UTF-8">\n<title>Fran\xc3\xa7ois Hollande \xe2\x80\x94 Wikip\xc3\xa9dia</title>\n<script>(function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limite

Ouch! You get the raw HTML code of the webpage. If you try to deal with it without tools, you will be there all night. Instead, use the [beautiful soup 4](https://www.crummy.com/software/BeautifulSoup/bs4/doc/) *external* library. You will find more info about it [here](../../2.python/2.python_advanced/05.Scraping/1.beautifulsoup_basic.ipynb) and [here](../../2.python/2.python_advanced/05.Scraping/2.beautifulsoup_advanced.ipynb)

Using the Quickstart section, start by importing the library and loading the output of your `get_text()` function.

Use the `prettify()` function and print it to take a look. You will start the actual parsing in the next step.

In [12]:
from bs4 import BeautifulSoup

soup = BeautifulSoup(wiki_html, 'html.parser')

print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-sticky-header-enabled vector-toc-available" dir="ltr" lang="fr">
 <head>
  <meta charset="utf-8"/>
  <title>
   François Hollande — Wikipédia
  </title>
  <script>
   (function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-conte

That looks better but you need to extract the right part of the webpage: the text of the first paragraph.

It is a bit tricky because Wikipedia pages slightly differ in structure from one language to the next. We cannot simply get the text for the first HTML paragraph.

You will start by getting all the HTML paragraphs from the HTML source and saving them in the `paragraphs` variable.

Use the documentation or google the appropriate keywords.

In [13]:
paragraphs = soup.find_all("p")

print(paragraphs)


[<p>Pour les articles homonymes, voir <a class="mw-disambig" href="/wiki/Hollande_(homonymie)" title="Hollande (homonymie)">Hollande (homonymie)</a>.
</p>, <p class="mw-empty-elt">
</p>, <p><b>François Hollande</b> <span class="API nowrap" style="font-family:'Segoe UI','DejaVu Sans','Lucida Grande','Lucida Sans Unicode','Arial Unicode MS','Hiragino Kaku Gothic Pro',sans-serif;" title="Alphabet phonétique international">[<a class="mw-redirect" href="/wiki/API_f" title="API f"><span title="[f] « f » dans « fête ».">f</span></a><a class="mw-redirect" href="/wiki/API_%CA%81" title="API ʁ"><span title="[ʁ] « r » dans « roue ».">ʁ</span></a><a class="mw-redirect" href="/wiki/API_%C9%91%CC%83" title="API ɑ̃"><span title="[ɑ̃] « an » dans « sans ».">ɑ̃</span></a><a class="mw-redirect" href="/wiki/API_s" title="API s"><span title="[s] en français « s » dans « sa » ; ailleurs avec la langue un peu plus en arrière (tel le basque : « s » dans « euskara »).">s</span></a><a class="mw-redirect" href=

If you try different urls, you might find that the paragraph you want may be at a different index each time.

That is where you need to be clever and ask yourself what would be a reliable way to identify the right index ie. which string matches only the first paragraph whatever the language...

Spend a good 30 minutes on the problem and brainstorm with your fellow learners. If you come out empty handed, ask your coach.

1. Loop over the HTML paragraphs
2. When you have identified the correct one:
   * Store the [text](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#output) inside the `first_paragraph` variable
   * Exit the loop

In [14]:
# We will only look for the first paragraph in the main content of the page
main_content = soup.find("div", class_="mw-content-ltr")

paragraphs = main_content.find_all("p")

first_paragraph = None

for paragraph in paragraphs:
      # Look for a <b> tag in the paragraph
      bold_tag = paragraph.find("b")

      # If we find the <b> tag and is not empty, then we assume that we are in the first paragraph of the main content
      if bold_tag and bold_tag.get_text().rstrip() != "":
         first_paragraph = paragraph.get_text()
         break

print(first_paragraph)

François Hollande [fʁɑ̃swa ɔlɑ̃d][n 3] Écouterⓘ, né le 12 août 1954 à Rouen (Seine-Inférieure), est un haut fonctionnaire et homme d'État français. Il est président de la République française du 15 mai 2012 au 14 mai 2017.



At this stage, you can create a function to maintain consistency in your code. We will give you its *skeleton*, you will copy the code you wrote and make it work inside a function.

Don't forget to test your function.

In [15]:
def get_first_paragraph(wikipedia_url):
   wiki_response = requests.get(wikipedia_url)

   if wiki_response.status_code != 200:
        print(f"Error {wiki_response.status_code} while scrapping URL => {wikipedia_url}")
        print(wiki_response.content)
        return None
   
   wiki_html = wiki_response.content

   soup = BeautifulSoup(wiki_html, 'html.parser')

   # We will only look for the first paragraph in the main content of the page 
   main_content = soup.find("div", class_="mw-content-ltr")

   paragraphs = main_content.find_all("p")
   
   first_paragraph = None

   for paragraph in paragraphs:
      # Look for a <b> tag in the paragraph
      bold_tag = paragraph.find("b")

      # If we find the <b> tag and is not empty, then we assume that we are in the first paragraph of the main content
      if bold_tag and bold_tag.get_text().rstrip() != "":
         first_paragraph = paragraph.get_text()
         break
  
   return first_paragraph

In [16]:
#first_paragraph = get_first_paragraph(first_french_leader["wikipedia_url"])
first_paragraph = get_first_paragraph("https://en.wikipedia.org/wiki/Barack_Obama")

print(first_paragraph)

Barack Hussein Obama II[a] (born August 4, 1961) is an American politician who was the 44th president of the United States from 2009 to 2017. A member of the Democratic Party, he was the first African American president in American history. Obama previously served as a U.S. senator representing Illinois from 2005 to 2008 and as an Illinois state senator from 1997 to 2004.



### 2a. Regular expressions to the rescue

Now that you have extracted the content of the first paragraph, the only thing that remains to finish your Wikipedia scraper is to sanitize the output.

Indeed some Wikipedia references, HTML code, phonetic pronunciation etc. may linger. You might find *regular expressions* handy to get rid of them and obtain pristine text. You will find some useful documentation about regular expressions [here](../../2.python/2.python_advanced/03.Regex/regex.ipynb)

Once you have one of your regex working online, try it in the cell below. 

Hints: 
* Check the `sub()` method documentation.
* Make sure to test urls in different languages. Some may look good but other do not.

In [17]:
import re

def clean_first_paragraph(paragraph: str):
    if not str:
        return None
    
    patterns_replacements = [
        {
            "pattern": r"\/.*?ⓘ; ",
            "replacement": ""
        },
        {
            "pattern": r" \(.*?ⓘ\)",
            "replacement": ""        
        },
        { 
            "pattern": r"\(.*?ⓘ; ",
            "replacement": "("
        },
        {
            "pattern": r"\(/.*?; ",
            "replacement": "("            
        },
        { 
            "pattern": r" \[.*?ⓘ",
            "replacement": ""
        },
        { 
            "pattern": r"\[\w\]",
            "replacement": ""
        }
    ]

    cleaned_paragraph = paragraph

    for pattern_replacement in patterns_replacements:
        cleaned_paragraph = re.sub(pattern_replacement["pattern"], pattern_replacement["replacement"], cleaned_paragraph)

    return cleaned_paragraph.rstrip()

first_paragraph = get_first_paragraph(first_french_leader["wikipedia_url"])
cleaned_paragraph = clean_first_paragraph(first_paragraph)

print(cleaned_paragraph)

François Hollande, né le 12 août 1954 à Rouen (Seine-Inférieure), est un haut fonctionnaire et homme d'État français. Il est président de la République française du 15 mai 2012 au 14 mai 2017.


Overwrite the `get_first_paragraph()` function by applying your regex to the first paragraph before returning it.

In [18]:
def get_first_paragraph(wikipedia_url: str):
    wiki_response = requests.get(wikipedia_url)

    if wiki_response.status_code != 200:
        print(f"Error {wiki_response.status_code} while scrapping URL => {wikipedia_url}")
        print(wiki_response.content)
        return ""
   
    wiki_html = wiki_response.content

    soup = BeautifulSoup(wiki_html, 'html.parser')

    # We will only look for the first paragraph in the main content of the page 
    main_content = soup.find("div", class_ = "mw-content-ltr")

    # Some pages use different class for the main content, let's try that
    if not main_content:
        print("Didn't find mw-content-ltr, trying mw-content-rtl")
        main_content = soup.find("div", class_ = "mw-content-rtl")

    if main_content:
        # Get all the pragraphs from the main content section
        paragraphs = main_content.find_all("p")
    
    if not paragraphs:
       # As a backup, we get all the pragraphs from the page
       print("Last resource, getting all the paragraphs from the page")
       paragraphs = soup.find_all("p")
   
    if paragraphs:
        print(f"Number of paragraphs: {len(paragraphs)}")

        for paragraph in paragraphs:
            # Look for a <b> tag in the paragraph
            bold_tag = paragraph.find("b")

            # If we find the <b> tag and is not empty, then we assume that we are in the first paragraph of the main content
            if bold_tag and bold_tag.get_text().rstrip() != "":
                # Clean the content of the paragraph before returning it
                return clean_first_paragraph(paragraph.get_text().rstrip())
            
    return ""

#first_paragraph = get_first_paragraph(first_french_leader["wikipedia_url"])
first_paragraph = get_first_paragraph("https://en.wikipedia.org/wiki/Zachary_Taylor")

print(first_paragraph)


Number of paragraphs: 85
Zachary Taylor (November 24, 1784 – July 9, 1850) was an American military officer and politician who was the 12th president of the United States, serving from 1849 until his death in 1850. Taylor was a career officer in the United States Army, rising to the rank of major general and becoming a national hero for his victories in the Mexican–American War. As a result, he won election to the White House despite his vague political beliefs. His top priority as president was to preserve the Union. He died 16 months into his term from a stomach disease. Taylor had the third-shortest presidential term in U.S. history and was the third president whose death has been traced to poor sanitation in Washington DC.


Come up with other regexes to capture other patterns and sanitize the outputs completely. Modify your `get_first_paragraph()` function accordingly.

In [19]:
# Extra sanitation implemented already in previous step

first_paragraph = get_first_paragraph(first_french_leader["wikipedia_url"])

print(first_paragraph)

Number of paragraphs: 140
François Hollande, né le 12 août 1954 à Rouen (Seine-Inférieure), est un haut fonctionnaire et homme d'État français. Il est président de la République française du 15 mai 2012 au 14 mai 2017.


## 3. Putting it all together

Let's go back to your `get_leaders()` function and update it with an *inner* loop over each leader. You will query the url provided and extract the first paragraph using the `get_first_paragraph()` function you just finished. You will then update that `leader`'s dictionary and move on to the next one.

Notice, the rest of the code should not change since you modify the leader's data one by one.

In [20]:
def get_leaders():
    api_root_url = "https://country-leaders.onrender.com"
    cookie_endpoint = "cookie"
    countries_endpoint = "countries"
    leaders_endpoint = "leaders"

    # Get cookie from the API
    cookie_response = requests.get(f"{api_root_url}/{cookie_endpoint}")

    if cookie_response.status_code != 200:
        print(f"Error {cookie_response.status_code} while callling API => {api_root_url}/{cookie_endpoint}")
        return None
    
    cookies = cookie_response.cookies

    # Get list of countries from the API
    countries_response = requests.get(
        f"{api_root_url}/{countries_endpoint}",
        cookies = cookies
    )

    if countries_response.status_code != 200:
        print(f"Error {countries_response.status_code} while callling API => {api_root_url}/{countries_endpoint}")
        print(countries_response.content)
        return None

    countries = countries_response.json()
    leaders_per_country = {}
    
    # Get list of leaders per country from the API
    for country in countries:
        leaders_response = requests.get(
            f"{api_root_url}/{leaders_endpoint}",
            cookies = cookies,
            params = {"country": country}
        )

        if leaders_response.status_code == 200:
            leaders_per_country[country] = leaders_response.json()

            # For each leader, get the extra info from Wikipedia
            for leader in leaders_per_country[country]:
                print(leader["wikipedia_url"])
                leader["wikipedia_intro"] = get_first_paragraph(leader["wikipedia_url"])
    
    return leaders_per_country

In [21]:
leaders = get_leaders()

print(leaders)

https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Hollande
Number of paragraphs: 140
https://fr.wikipedia.org/wiki/Nicolas_Sarkozy
Number of paragraphs: 195
https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Mitterrand
Number of paragraphs: 169
https://fr.wikipedia.org/wiki/Charles_de_Gaulle
Number of paragraphs: 244
https://fr.wikipedia.org/wiki/Jacques_Chirac
Number of paragraphs: 266
https://fr.wikipedia.org/wiki/Val%C3%A9ry_Giscard_d%27Estaing
Number of paragraphs: 245
https://fr.wikipedia.org/wiki/Georges_Pompidou
Number of paragraphs: 81
https://fr.wikipedia.org/wiki/Adolphe_Thiers
Number of paragraphs: 200
https://fr.wikipedia.org/wiki/Napol%C3%A9on_III
Number of paragraphs: 272
https://fr.wikipedia.org/wiki/Paul_Doumer
Number of paragraphs: 121
https://fr.wikipedia.org/wiki/Alain_Poher
Number of paragraphs: 37
https://fr.wikipedia.org/wiki/Albert_Lebrun
Number of paragraphs: 73
https://fr.wikipedia.org/wiki/Ren%C3%A9_Coty
Number of paragraphs: 46
https://fr.wikipedia.org/wiki/Vincent_Auriol

Does the function crash in the middle of the loop? Chances are the cookies have expired while looping over the leaders.

Modify your function with an *exception* or check if the `status_code` is a cookie error. In either case, get new cookies and query the api again.

If your code did not crash,

In [22]:
def api_get_cookies(api_root_url: str, cookie_endpoint: str):
    # Get cookie from the API
    cookie_response = requests.get(f"{api_root_url}/{cookie_endpoint}")

    if cookie_response.status_code != 200:
        print(f"Error {cookie_response.status_code} while callling API => {api_root_url}/{cookie_endpoint}")
        print(cookie_response.content)
        return None
    
    return cookie_response.cookies

def get_leaders():
    api_root_url = "https://country-leaders.onrender.com"
    cookie_endpoint = "cookie"
    countries_endpoint = "countries"
    leaders_endpoint = "leaders"

    cookies = api_get_cookies(api_root_url, cookie_endpoint)
    if not cookies:
        return

    # Get list of countries from the API
    countries_response = requests.get(
        f"{api_root_url}/{countries_endpoint}",
        cookies = cookies
    )

    if countries_response.status_code != 200:
        print(f"Error {countries_response.status_code} while callling API => {api_root_url}/{countries_endpoint}")
        print(countries_response.content)
        return None

    countries = countries_response.json()
    print(f"Countries: {countries}")

    leaders_per_country = {}
    
    # Get list of leaders per country from the API
    for country in countries:
        print(f"Processing country: {country}")

        leaders_response = requests.get(
            f"{api_root_url}/{leaders_endpoint}",
            cookies = cookies,
            params = {"country": country}
        )

        # If cookie is expired, lets get a new one and call the leaders endpoint again
        if leaders_response.status_code == 403:
            print("Expired cookie, getting new one")
            
            cookies = api_get_cookies(api_root_url, cookie_endpoint)

            leaders_response = requests.get(
                f"{api_root_url}/{leaders_endpoint}",
                cookies = cookies,
                params = {"country": country}
            )

        if leaders_response.status_code == 200:
            leaders_per_country[country] = leaders_response.json()

            print(f"{len(leaders_per_country[country])} leaders found for country {country}")
            # For each leader, get the extra info from Wikipedia
            for leader in leaders_per_country[country]:
                print(leader["wikipedia_url"])
                leader["wikipedia_intro"] = get_first_paragraph(leader["wikipedia_url"])
        else:
            print(f"Error {leaders_response.status_code} while callling API => {api_root_url}/{leaders_endpoint}")
            print(leaders_response.content)
    
    return leaders_per_country


Check the output of your function again.

In [23]:
leaders = get_leaders()

print(leaders)

Countries: ['fr', 'be', 'ma', 'us', 'ru']
Processing country: fr
31 leaders found for country fr
https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Hollande
Number of paragraphs: 140
https://fr.wikipedia.org/wiki/Nicolas_Sarkozy
Number of paragraphs: 195
https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Mitterrand
Number of paragraphs: 169
https://fr.wikipedia.org/wiki/Charles_de_Gaulle
Number of paragraphs: 244
https://fr.wikipedia.org/wiki/Jacques_Chirac
Number of paragraphs: 266
https://fr.wikipedia.org/wiki/Val%C3%A9ry_Giscard_d%27Estaing
Number of paragraphs: 245
https://fr.wikipedia.org/wiki/Georges_Pompidou
Number of paragraphs: 81
https://fr.wikipedia.org/wiki/Adolphe_Thiers
Number of paragraphs: 200
https://fr.wikipedia.org/wiki/Napol%C3%A9on_III
Number of paragraphs: 272
https://fr.wikipedia.org/wiki/Paul_Doumer
Number of paragraphs: 121
https://fr.wikipedia.org/wiki/Alain_Poher
Number of paragraphs: 37
https://fr.wikipedia.org/wiki/Albert_Lebrun
Number of paragraphs: 73
https://fr.wikipe

Well done! It took a while however... Let's speed things up. The main *bottleneck* is the loop. We call on the Wikipedia website many times.

You will use the same *session* to call all the wikipedia pages. Check the *Advanced Usage* section of the Requests module's documentation.

Start by modifying the `get_first_paragraph()` function to accept a session parameter and adjust the `get()` method call.

In [34]:
def get_first_paragraph(session, wikipedia_url: str):
    wiki_response = session.get(wikipedia_url)

    if wiki_response.status_code != 200:
        print(f"Error {wiki_response.status_code} while scrapping URL => {wikipedia_url}")
        print(wiki_response.content)
        return ""
   
    wiki_html = wiki_response.content

    soup = BeautifulSoup(wiki_html, 'html.parser')

    # We will only look for the first paragraph in the main content of the page 
    main_content = soup.find("div", class_ = "mw-content-ltr")

    # Some pages use different class for the main content, let's try that
    if not main_content:
        print("Didn't find mw-content-ltr, trying mw-content-rtl")
        main_content = soup.find("div", class_ = "mw-content-rtl")

    if main_content:
        # Get all the pragraphs from the main content section
        paragraphs = main_content.find_all("p")
    
    if not paragraphs:
       # As a backup, we get all the pragraphs from the page
       print("Last resource, getting all the paragraphs from the page")
       paragraphs = soup.find_all("p")
   
    if paragraphs:
        print(f"Number of paragraphs: {len(paragraphs)}")

        for paragraph in paragraphs:
            # Look for a <b> tag in the paragraph
            bold_tag = paragraph.find("b")

            # If we find the <b> tag and is not empty, then we assume that we are in the first paragraph of the main content
            if bold_tag and bold_tag.get_text().rstrip() != "":
                # Clean the content of the paragraph before returning it
                return clean_first_paragraph(paragraph.get_text().rstrip())
            
    return ""

Modify your `get_leaders()` function to make use of a single session for all the Wikipedia calls.
1. create a `Session` object outside of the loop over countries.
2. pass it to the `get_first_paragraph()` function as an argument.

In [35]:
def api_get_cookies(session, api_root_url: str, cookie_endpoint: str):
    # Get cookie from the API
    cookie_response = session.get(f"{api_root_url}/{cookie_endpoint}")

    if cookie_response.status_code != 200:
        print(f"Error {cookie_response.status_code} while callling API => {api_root_url}/{cookie_endpoint}")
        print(cookie_response.content)
        return None
    
    return cookie_response.cookies

def get_leaders(session):
    api_root_url = "https://country-leaders.onrender.com"
    cookie_endpoint = "cookie"
    countries_endpoint = "countries"
    leaders_endpoint = "leaders"

    cookies = api_get_cookies(session, api_root_url, cookie_endpoint)
    if not cookies:
        return

    # Get list of countries from the API
    countries_response = session.get(
        f"{api_root_url}/{countries_endpoint}",
        cookies = cookies
    )

    if countries_response.status_code != 200:
        print(f"Error {countries_response.status_code} while callling API => {api_root_url}/{countries_endpoint}")
        print(countries_response.content)
        return None

    countries = countries_response.json()
    print(f"Countries: {countries}")

    leaders_per_country = {}
    
    # Get list of leaders per country from the API
    for country in countries:
        print(f"Processing country: {country}")

        leaders_response = session.get(
            f"{api_root_url}/{leaders_endpoint}",
            cookies = cookies,
            params = {"country": country}
        )

        # If cookie is expired, lets get a new one and call the leaders endpoint again
        if leaders_response.status_code == 403:
            print("Expired cookie, getting new one")
            
            cookies = api_get_cookies(session, api_root_url, cookie_endpoint)

            leaders_response = session.get(
                f"{api_root_url}/{leaders_endpoint}",
                cookies = cookies,
                params = {"country": country}
            )

        if leaders_response.status_code == 200:
            leaders_per_country[country] = leaders_response.json()

            print(f"{len(leaders_per_country[country])} leaders found for country {country}")
            # For each leader, get the extra info from Wikipedia
            for leader in leaders_per_country[country]:
                print(leader["wikipedia_url"])
                leader["wikipedia_intro"] = get_first_paragraph(session, leader["wikipedia_url"])
        else:
            print(f"Error {leaders_response.status_code} while callling API => {api_root_url}/{leaders_endpoint}")
            print(leaders_response.content)
    
    return leaders_per_country

Test your new functions.



In [36]:
session = requests.Session()

leaders = get_leaders(session)

print(leaders)

Countries: ['ma', 'us', 'ru', 'fr', 'be']
Processing country: ma
4 leaders found for country ma
https://ar.wikipedia.org/wiki/%D9%85%D8%AD%D9%85%D8%AF_%D8%A7%D9%84%D8%B3%D8%A7%D8%AF%D8%B3_%D8%A8%D9%86_%D8%A7%D9%84%D8%AD%D8%B3%D9%86
Didn't find mw-content-ltr, trying mw-content-rtl
Number of paragraphs: 161
https://ar.wikipedia.org/wiki/%D8%A7%D9%84%D8%AD%D8%B3%D9%86_%D8%A7%D9%84%D8%AB%D8%A7%D9%86%D9%8A_%D8%A8%D9%86_%D9%85%D8%AD%D9%85%D8%AF
Didn't find mw-content-ltr, trying mw-content-rtl
Number of paragraphs: 150
https://ar.wikipedia.org/wiki/%D9%85%D8%AD%D9%85%D8%AF_%D8%A7%D9%84%D8%AE%D8%A7%D9%85%D8%B3_%D8%A8%D9%86_%D9%8A%D9%88%D8%B3%D9%81
Didn't find mw-content-ltr, trying mw-content-rtl
Number of paragraphs: 30
https://ar.wikipedia.org/wiki/%D8%A7%D9%84%D9%82%D8%A7%D8%A6%D9%85_%D8%A8%D8%A3%D9%85%D8%B1_%D8%A7%D9%84%D9%84%D9%87_%D8%A7%D9%84%D8%B3%D8%B9%D8%AF%D9%8A
Didn't find mw-content-ltr, trying mw-content-rtl
Number of paragraphs: 5
Processing country: us
45 leaders found for cou

## 4. Saving your hard work

The final step is to save the ``leaders_per_country`` dictionary in the `leaders.json` file using the [json](https://docs.python.org/3/library/json.html) module. Check out the `with` statement.

In [39]:
import json

# Serializing json
json_object = json.dumps(leaders, indent=4)

# Writing to file
with open("leaders.json", "w") as outfile:
    outfile.write(json_object)


Make sure the file can be read back. Write the code to read the file. And check the variables are the same.

In [41]:
with open('leaders.json', 'r') as openfile:
    json_object = json.load(openfile)

print(json_object)
print(json_object == leaders)

{'ma': [{'id': 'Q57553', 'first_name': 'Mohammed', 'last_name': 'None', 'birth_date': '1963-08-21', 'death_date': None, 'place_of_birth': 'Rabat', 'wikipedia_url': 'https://ar.wikipedia.org/wiki/%D9%85%D8%AD%D9%85%D8%AF_%D8%A7%D9%84%D8%B3%D8%A7%D8%AF%D8%B3_%D8%A8%D9%86_%D8%A7%D9%84%D8%AD%D8%B3%D9%86', 'start_mandate': '1999-07-23', 'end_mandate': None, 'wikipedia_intro': 'مُحمد السادس بن الحسن الثاني العلوي (مواليد 21 أغسطس 1963) هو ملك المملكة المغربية منذ عام 1999 والملك الثالث والعشرون للمغرب من سلالة العلويين الفيلاليين، تولى الحكم خلفًا لوالده الملك الحسن الثاني بعد وفاته، وبويع ملكًا يوم الجمعة 9 ربيع الثاني سنة 1420 هـ الموافق 23 يوليو 1999 بالقصر الملكي بالرباط.'}, {'id': 'Q69103', 'first_name': 'Hassan', 'last_name': 'None', 'birth_date': '1929-07-09', 'death_date': '1999-07-20', 'place_of_birth': 'Rabat', 'wikipedia_url': 'https://ar.wikipedia.org/wiki/%D8%A7%D9%84%D8%AD%D8%B3%D9%86_%D8%A7%D9%84%D8%AB%D8%A7%D9%86%D9%8A_%D8%A8%D9%86_%D9%85%D8%AD%D9%85%D8%AF', 'start_mandate': 

Make a function `save(leaders_per_country)` to call this code easily.

In [42]:
def save(leaders_dictionary, filepath):
    # Serializing json
    json_object = json.dumps(leaders_dictionary, indent=4)

    # Writing to file
    with open(filepath, "w") as outfile:
        outfile.write(json_object)

In [43]:
save(leaders, "leaders.json")

## 5. Tidy things up in a stand-alone python script

Congratulations! You now have a working scraper! However, your code is scattered throughout this notebook along side the tutorials. Hardly production ready...

Copy and paste what you need in a separate `leaders_scraper.py` file.
Make sure it works by calling `python3 leaders_scraper.py`

## (Optional) To go further

If you want to practice scraping, you can read this section and tackle the exercises.

1. Restructure your code by using OOP (see ReadMe).
2. You have noticed the API returns very partial results for country leaders. Many are missing. Overwrite the `get_leaders()` function to get its list from Wikipedia and extract their *personal details* from the frame on the side.

Good luck!